# Post Migration Delta 

In [2]:
from Preamble import * 
print(ts_host)
print(ts_host2)

https://cmcmarkets.thoughtspot.cloud
https://cmcmarkets.thoughtspot.cloud


In [25]:
import pandas as pd
import pytz
import datetime as dt
from migration_tools import HTTPClient

source_ts_url = "https://champagne2.thoughtspotstaging.cloud/"
source_username = "migration_tools"
source_password = "really-super-secret-password!"
backup_date = dt.datetime(2012, 11, 1)
backup_date = dt.datetime(2022, 8, 1)

ts = HTTPClient(ts_url=source_ts_url)
r = ts.login(source_username, source_password)
r.raise_for_status()

r = ts.session_info()
tz_name = r.json()["timezone"]
timestamp = backup_date.replace(tzinfo=pytz.timezone(tz_name)).timestamp() * 1000

r = ts.user_list()
df = (
    pd
    .json_normalize(r.json())
    # df.created and df.modified are in milliseconds
    .query("created > @timestamp", local_dict={"timestamp": timestamp})
    .query("modified > @timestamp", local_dict={"timestamp": timestamp})
)

df

name                    displayName  \
36                           socgroup          Sharing of Connection   
130  dragos.georgescu@thoughtspot.com               Dragos Georgescu   
240                   migration_tools             PS Migration Tools   
241                          NewUsr19                       NewUsr19   
404                           Bharath                      Bharath G   
546                              kaya                           Kaya   
666                             Ankit                          Ankit   
871     aditya.wadher@thoughtspot.com  aditya.wadher@thoughtspot.com   
883                        UpdateTest                     UpdateTest   
897      jens.englert@thoughtspot.com                   jens.englert   

    description        created       modified principalTypeEnum  \
36               1663927611561  1663928215404       LOCAL_GROUP   
130         NaN  1663593255477  1664390229213        LOCAL_USER   
240         NaN  1664722450958  1664722451131        LOCAL_USER   
241         NaN  1660884681575  1660884711431        LOCAL_USER   
404         NaN  1663926823540  1663926902091        LOCAL_USER   
546         NaN  1661375197121  1661375197332        LOCAL_USER   
666         NaN  1663927759580  1663927759918        LOCAL_USER   
871              1661322214188  1661429063899        LOCAL_USER   
883         NaN  1660139208548  1660139558697        LOCAL_USER   
897         NaN  1664205916016  1664205916016         SAML_USER   

                                        groupNames    visibility  activate  \
36                                              []       DEFAULT     False   
130        [Administrator, All, Demo Retail Group]       DEFAULT     False   
240        [Administrator, All, Demo Retail Group]  NON_SHARABLE     False   
241                   [Demo Retail Group, G1, All]       DEFAULT     False   
404                       [All, Demo Retail Group]       DEFAULT     False   
546        [Demo Retail Group, Administrator, All]  NON_SHARABLE     False   
666             [All, Demo Retail Group, socgroup]       DEFAULT     False   
871        [Demo Retail Group, Administrator, All]       DEFAULT     False   
883        [Demo Retail Group, Administrator, All]       DEFAULT     False   
897  [All, friends_of_cs_tools, Demo Retail Group]       DEFAULT     False   

                                 mail  
36                                NaN  
130  dragos.georgescu@thoughtspot.com  
240   nicholas.cooper@thoughtspot.com  
241   deepthi.nagaraj@thoughtspot.com  
404      bharathram.g@thoughtspot.com  
546   nicholas.cooper@thoughtspot.com  
666   ankit.choudhary@thoughtspot.com  
871     aditya.wadher@thoughtspot.com  
883           honey.k@thoughtspot.com  
897      jens.englert@thoughtspot.com

## Gather Object Metadata for new and modified Objects

In [3]:
## specify backup date

print("Backup Year: ")
backup_year = input()
print("Backup Month: ")
backup_month = input()
print("Backup Day: ")
backup_day = input()
import datetime
backupdate = (datetime.datetime(int(backup_year or 0),int(backup_month or 0),int(backup_day or 0),0,0) - datetime.datetime(1970,1,1)).total_seconds()

import pandas as pd
# Start Session 

sess = requests.Session()

# Login via API

login(sess)

#Download modeling file
"""
Modelingfile = GetModelingFile(sess)
with open("Modelingfile.tsv", "w") as f:
    f.write(Modelingfile.text)
"""
# Users  7.2.1
try:
    UserData = lstUsers(sess).json()    
    df = json_normalize(UserData)
    df = df[['header.id','header.name','header.created','header.modified','header.displayName','userContent.userProperties.mail','assignedGroups']]
    df['created_flag'] = df['header.created'] > backupdate * 1000
    new_user_objects = df[df['created_flag']==True]
    df['modified_flag'] = df['header.modified'] > backupdate * 1000
    modified_user_objects = df[df['modified_flag']==True]
    print("Number of Users", len(df.index))
    print("Number of Users created " ,len(new_user_objects.index))
    print("Number of Users modified " , len(modified_user_objects.index))
    new_user_objects.to_csv(".//data//new//Users_created_Cloud.txt", index = False,encoding='utf8')
    modified_user_objects.to_csv(".//data//modified//Users_modified_Cloud.txt", index = False,encoding='utf8')
    df.to_csv(".//data//Users.txt", index = False,encoding='utf8')
except:
    pass
# Users  

UserData = lstUserLists(sess).json()    
df = json_normalize(UserData)
print("Number of Users + Groups", len(df.index))

df['created_flag'] = df['created'] > backupdate * 1000
new_user_objects = df[df['created_flag']==True]
df['modified_flag'] = df['modified'] > backupdate * 1000
modified_user_objects = df[df['modified_flag']==True]
print("Number of Users", len(df.index))
print("Number of Users created " ,len(new_user_objects.index))
print("Number of Users modified " , len(modified_user_objects.index))
UserList_created = new_user_objects['id'].to_list()
UserList_modified = modified_user_objects['id'].to_list()
new_user_objects.to_csv(".//data//new//Users_created.txt", index = False,encoding='utf8')
modified_user_objects.to_csv(".//data//modified//Users_modified.txt", index = False,encoding='utf8')
df.to_csv(".//data//Users.txt", index = False,encoding='utf8')


#create mapping table to map user_id and name
try:
    UserData = lstUsers(sess).json()    
    df = json_normalize(UserData)
    map_user = df[['header.id','header.name']]
    map_user.to_csv(".//data//mapping_users.txt", index = False,encoding='utf8')
except:
    print("couldn't map users from user id")
    pass
#end of mapping section

# Get high level information about Meta data objects 

# Liveboards #######################################################################

PinboardHeader = listPinboards(sess).json()
df = json_normalize(PinboardHeader)
df = pd.merge(map_user,df, left_on='header.id', right_on='author')
df['date_created'] = pd.to_datetime(df['created']/1000,unit='s')
df['date_modified'] = pd.to_datetime(df['modified']/1000,unit='s')
df['created_flag'] = df['created'] > backupdate * 1000
new_liveboard_objects = df[df['created_flag']==True]
df['modified_flag'] = df['modified'] > backupdate * 1000
modified_liveboard_objects = df[df['modified_flag']==True]
#modified_liveboard_objects['timestamp_modified'] = time.strftime('%Y-%m-%d %H:%M:%S', time.localtime(int(df['modified']))
# modified_objects
print("Number of Liveboards", len(df.index))
print("Number of Liveboards created " ,len(new_liveboard_objects.index))
print("Number of Liveboards modified " , len(modified_liveboard_objects.index))
PinList_created = new_liveboard_objects['id'].to_list()
PinList_modified = modified_liveboard_objects['id'].to_list()
df.to_csv(".//data//Pinboards.txt", index = False,encoding='utf8')
new_liveboard_objects.to_csv(".//data//new//Pinboards_created.txt", index = False,encoding='utf8')
modified_liveboard_objects.to_csv(".//data//modified//Pinboards_modified.txt", index = False,encoding='utf8')



# Answers #######################################################################
try:
    AnswerHeader = listAnswers(sess).json()
    df = json_normalize(AnswerHeader)
    df = pd.merge(map_user,df, left_on='header.id', right_on='author')
    df['date_created'] = pd.to_datetime(df['created']/1000,unit='s')
    df['date_modified'] = pd.to_datetime(df['modified']/1000,unit='s')
    df['created_flag'] = df['created'] > backupdate * 1000
    new_objects = df[df['created_flag']==True]
    df['modified_flag'] = df['modified'] > backupdate * 1000
    modified_objects = df[df['modified_flag']==True]

    print("Number of Answers", len(df.index))
    print("Number of Answers created " ,len(new_objects.index))
    print("Number of Answers modified " , len(modified_objects.index))
    AnswerList_created = new_objects['id'].to_list()
    AnswerList_modified = modified_objects['id'].to_list()

    df.to_csv(".//data//Answers.txt", index = False,encoding='utf8')
    new_objects.to_csv(".//data//new//Answers_created.txt", index = False,encoding='utf8')
    modified_objects.to_csv(".//data//modified//Answers_modified.txt", index = False,encoding='utf8')
except:
    print("No Answers available")

# Worksheets #######################################################################

WorksheetHeader = listWorksheets(sess).json()
df = json_normalize(WorksheetHeader)
df = pd.merge(map_user,df, left_on='header.id', right_on='author')
df['date_created'] = pd.to_datetime(df['created']/1000,unit='s')
df['date_modified'] = pd.to_datetime(df['modified']/1000,unit='s')
df['created_flag'] = df['created'] > backupdate * 1000
new_worksheet_objects = df[df['created_flag']==True]
df['modified_flag'] = df['modified'] > backupdate * 1000
modified_worksheet_objects = df[df['modified_flag']==True]

print("Number of Worksheets", len(df.index))
print("Number of Worksheets created " ,len(new_worksheet_objects.index))
print("Number of Worksheets modified " , len(modified_worksheet_objects.index))
WSList_created = new_worksheet_objects['id'].to_list()
WSList_modified = modified_worksheet_objects['id'].to_list()

df.to_csv(".//data//Worksheets.txt", index = False,encoding='utf8')
new_worksheet_objects.to_csv(".//data//new//Worksheets_created.txt", index = False,encoding='utf8')
modified_worksheet_objects.to_csv(".//data//modified//Worksheets_modified.txt", index = False,encoding='utf8')


# Tables #######################################################################

TablesHeader = listTables(sess).json()
df = json_normalize(TablesHeader)
df = pd.merge(map_user,df, left_on='header.id', right_on='author')
df['date_created'] = pd.to_datetime(df['created']/1000,unit='s')
df['date_modified'] = pd.to_datetime(df['modified']/1000,unit='s')
df['created_flag'] = df['created'] > backupdate * 1000
new_table_objects = df[df['created_flag']==True]
df['modified_flag'] = df['modified'] > backupdate * 1000
modified_table_objects = df[df['modified_flag']==True]

print("Number of Tables", len(df.index))
print("Number of Tables created " ,len(new_table_objects.index))
print("Number of Tables modified " , len(modified_table_objects.index))
TableList_created = new_table_objects['id'].to_list()
TableList_modified = modified_table_objects['id'].to_list()

df.to_csv(".//data//Tables.txt", index = False,encoding='utf8')
new_table_objects.to_csv(".//data//new//Tables_created.txt", index = False,encoding='utf8')
modified_table_objects.to_csv(".//data//modified//Tables_modified.txt", index = False,encoding='utf8')

# View #######################################################################
try:
    ViewHeader = listViews(sess).json()
    df = json_normalize(ViewHeader)
    df = pd.merge(map_user,df, left_on='header.id', right_on='author')
    df['date_created'] = pd.to_datetime(df['created']/1000,unit='s')
    df['date_modified'] = pd.to_datetime(df['modified']/1000,unit='s')
    df['created_flag'] = df['created'] > backupdate * 1000
    new_objects = df[df['created_flag']==True]
    df['modified_flag'] = df['modified'] > backupdate * 1000
    modified_objects = df[df['modified_flag']==True]

    print("Number of Views", len(df.index))
    print("Number of Views created " ,len(new_objects.index))
    print("Number of Views modified " , len(modified_objects.index))
    ViewList_created = new_objects['id'].to_list()
    ViewList_modified = modified_objects['id'].to_list()

    df.to_csv(".//data//Views.txt", index = False,encoding='utf8')
    new_objects.to_csv(".//data//new//Views_created.txt", index = False,encoding='utf8')
    modified_objects.to_csv(".//data//modified//Views_modified.txt", index = False,encoding='utf8')
except:
    print("No View available")


## user defined tables

UserDefinedHeader = listUserDefTables(sess).json()
df = json_normalize(UserDefinedHeader)
df.to_csv("UserDefTables.txt", index = False,encoding='utf8')


# Logout
logout(sess)

Backup Year: 
2022
Backup Month: 
9
Backup Day: 
13

Call to '/callosum/v1/tspublic/v1/session/login' successfull! (204)

Call to '/callosum/v1/tspublic/v1/user' successfull! (200)
Number of Users 381
Number of Users created  0
Number of Users modified  0

Call to '/callosum/v1/tspublic/v1/user/list' successfull! (200)
Number of Users + Groups 424

Call to '/callosum/v1/tspublic/v1/user' successfull! (200)

Call to '/callosum/v1/tspublic/v1/metadata/listobjectheaders?type=PINBOARD_ANSWER_BOOK&category=ALL&sort=DEFAULT&offset=-1&batchsize=2000' successfull! (200)
Number of Liveboards 1343
Number of Liveboards created  53
Number of Liveboards modified  54

Call to '/callosum/v1/tspublic/v1/metadata/listobjectheaders?type=QUESTION_ANSWER_BOOK&category=ALL&sort=DEFAULT&offset=-1&batchsize=4000' successfull! (200)
Number of Answers 1391
Number of Answers created  65
Number of Answers modified  66

Call to '/callosum/v1/tspublic/v1/metadata/listobjectheaders?type=LOGICAL_TABLE&subtypes=%5BWO

<Response [204]>

create_user(rest_api_obj=ts, username=username, display_name=displayname,
                            email=email, groups_guid=group_guid)

## Get Permissions

In [27]:
# download all metaobjects a group can read
# Start Session
sess = requests.Session()
# Login via API
login(sess)

GroupData = lstGroups(sess).json()    
Group_df = json_normalize(GroupData)

GroupList = Group_df['header.id'].to_list()
# dict to print
json_print = {}
group_access_df = pd.DataFrame()
# for all groups in user list gather metaobjects
for i in GroupList:
    print(i)
    resp = lstGroupMetadataRead(sess,i).json()
    resp_norm = json_normalize(resp['headers'])
    print(resp_norm)
    resp_norm['access'] = "READ_ONLY"
    resp_norm['user_id'] = i
    # print user id into json for each metaobject user has access to
    group_access_df = pd.concat([group_access_df,resp_norm], ignore_index = True)
    
#Access_Groups = open("Access_Groups_readOnly.txt", "w")
#Access_Groups.write(group_access_df)
group_access_df = group_access_df[['id','name','access','user_id']]
grp_read = group_access_df
print("Read Only Access for Groups successfully downloaded")
# Logout
logout(sess)
grp_read = grp_read[grp_read['id'].isin(PinList_created)]
grp_read['type'] = 'LIVEBOARD'
grp_read


Call to '/callosum/v1/tspublic/v1/session/login' successfull! (204)

Call to '/callosum/v1/tspublic/v1/group' successfull! (200)
4881af30-aeee-49a3-9606-55cedeb23a66

Call to '/callosum/v1/tspublic/v1/metadata/listas?offset=-1&batchsize=2000&principalid=4881af30-aeee-49a3-9606-55cedeb23a66&minimumaccesslevel=READ_ONLY&type=USER_GROUP' successfull! (200)
Empty DataFrame
Columns: []
Index: []
2bec5a06-5068-471f-8afd-d61871c40207

Call to '/callosum/v1/tspublic/v1/metadata/listas?offset=-1&batchsize=2000&principalid=2bec5a06-5068-471f-8afd-d61871c40207&minimumaccesslevel=READ_ONLY&type=USER_GROUP' successfull! (200)
Empty DataFrame
Columns: []
Index: []
84b6709d-4b71-45df-aeed-da01c52ef1fb

Call to '/callosum/v1/tspublic/v1/metadata/listas?offset=-1&batchsize=2000&principalid=84b6709d-4b71-45df-aeed-da01c52ef1fb&minimumaccesslevel=READ_ONLY&type=USER_GROUP' successfull! (200)
Empty DataFrame
Columns: []
Index: []
6cb62f9c-9e89-42b6-a59d-be924c1aecf7

Call to '/callosum/v1/tspublic/v1/met

/var/folders/72/k44_gp394l5g9rc09_hz25180000gs/T/ipykernel_8581/1372184780.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  grp_read['type'] = 'LIVEBOARD'


id  \
6   c05a39dc-3838-435d-bec5-62ff16df290c   
7   e0029dda-0b40-46b8-9637-3d5464cac065   
8   3a443655-b544-473f-9df2-d44006899c3e   
9   ad96fb40-d9b6-4350-afab-e009b2f49c34   
10  c12cbc23-a419-49fd-be9f-0ba202c87281   
11  f74fee53-2892-4623-bead-a1464cc24b9d   
12  a17acd34-a77d-4c1f-ac1f-98efc1418a9c   
13  6b771d58-133a-4167-bd0e-c615d44a19b8   
14  de4fb9a2-8c9a-4a7e-a31f-8cadbb76bf5b   
15  8ffba0ac-2fde-4b71-b2ba-83ae2a742f2a   
16  c7ef6c8c-4ba8-40f4-8b4b-001a0cc6dc1b   
17  092f0716-e7aa-4bf1-b51b-a25aded568b3   
18  36645b1d-21bb-4f80-a14c-60dac32953f6   
19  400e954a-ec62-4553-9cd7-c38560ffdc08   
20  4db39dac-fbdd-40e8-b090-d7ccc78beb63   
21  af9fdf06-9452-45c0-9292-f62b11577b06   
22  453c93e9-4b59-4b64-ac51-f54ddbbc473d   
23  4dac9934-0f24-4138-a08f-f17ea54068ad   
24  9a173eb3-d3af-4238-ac61-d7c3d47f9072   
25  a5204dde-9c19-420c-8d22-eed5d6f0de4f   
26  4d3097cf-0629-4414-b292-9721a32f4dc2   
27  7b871a05-1f0c-444f-8f95-0e18423e7051   
28  5bacf773-cb63-4192-ba5c-b8b4fc0c8bcf   
29  94fd1b63-7d43-4074-97c4-e11229783da8   
30  cce6e2a4-4e7e-45b7-bed0-296086eb042e   
31  aa840b51-9e62-46f3-82ac-8b269b9a7ac0   
32  69ea12b1-d9af-494a-91fe-530faf40cca6   
33  8f675836-4e83-461e-bf6f-bdcd06b7defe   
34  afdb8960-feb0-4e3b-97c2-6c0d195bd3c2   
35  8e9a2786-c708-424a-80d9-dfa39204fbf2   
36  e927e2e9-ebe1-4649-9100-14be88e54349   
37  e35bb8e8-695d-4e32-bae0-fbf37bf545a2   
38  8827a47c-7198-4962-9798-c8d4bfd57dfb   
39  7dd9286c-671e-47b8-9dfb-fd113cfd99e4   
40  5198ad70-e6ef-41ae-bfbd-783596be4af1   
41  c97b0947-3f09-40c2-a3a8-c378d5e97f33   
42  da51f606-1eff-40d9-94aa-a29ac0bc8b15   
43  4534887d-3e70-466d-b130-dc349228ab78   
44  5019fc68-2868-481e-8327-228f9973bf36   
45  403143f9-ed6d-4e51-957c-35279d739bce   
46  8bc40756-242a-4f6e-8a95-034575fe5c52   
47  e76f5d64-e286-486d-85dc-2282f83ed5ab   
48  2f8a4c82-c95e-441d-ad2f-ce90d60c571d   
49  12a360c1-6880-4839-86cd-5e7cc8a897a3   
50  e6b239a6-5870-4e73-8bde-97363d73e440   
51  718e480b-c191-4a31-84ec-d1cc6754a9da   
52  c79e3244-10c8-4e33-90a5-9d77b1503103   
53  3570fb2e-48ab-4550-b97a-36c31fe188a6   
54  55baf16c-3075-4cde-867e-b10b62cedfc3   
55  7cad6069-93b7-4d6a-9c4a-efc632b13ef1   
56  0225b62d-35d0-458a-bd0a-e37b037f245c   
57  30662828-2b47-4138-a7cf-5acc0a0a966b   
58  9d29b03d-5c59-40d7-9761-edfb97a8424b   

                                                 name     access  \
6                                        Data Request  READ_ONLY   
7            Investments - Welcome Bonus Dashboard v2  READ_ONLY   
8                                 Country On boarding  READ_ONLY   
9                                           Jo's Book  READ_ONLY   
10        ZH Acquisition Dashboard - Marketing - Luna  READ_ONLY   
11                   Australia New account Conversion  READ_ONLY   
12                                       IAID Tracker  READ_ONLY   
13                                       Mary's board  READ_ONLY   
14                             Referral IAID tracking  READ_ONLY   
15                APAC Client Trading value dashboard  READ_ONLY   
16                    Copy of Monthly MI Report (SFC)  READ_ONLY   
17                               Revenue Distribution  READ_ONLY   
18                               Revenue Distribution  READ_ONLY   
19                                              Alpha  READ_ONLY   
20                                         Test -luna  READ_ONLY   
21                                Client PnL Analysis  READ_ONLY   
22                              Copy of Find Accounts  READ_ONLY   
23                                     Monthly CRM UK  READ_ONLY   
24                       Copy of Regional BD Swticher  READ_ONLY   
25                              Copy of Find Accounts  READ_ONLY   
26                             Top Traded Instruments  READ_ONLY   
27           Copy of Rebates Dashboard - Distribution  READ_ONLY   
28                                  SFC Since 1st May  READ_ONLY   
29                           

In [28]:
# download all metaobjects a group can modify
# Start Session
sess = requests.Session()
# Login via API
login(sess)

GroupData = lstGroups(sess).json()    
Group_df = json_normalize(GroupData)

GroupList = Group_df['header.id'].to_list()
# dict to print
json_print = {}
group_access_df = pd.DataFrame()
# for all groups in user list gather metaobjects
for i in GroupList:
    print(i)
    resp = lstGroupMetadataModify(sess,i).json()
    resp_norm = json_normalize(resp['headers'])
    #print(resp_norm)
    resp_norm['access'] = "MODIFY"
    resp_norm['user_id'] = i
    # print user id into json for each metaobject user has access to
    group_access_df = pd.concat([group_access_df,resp_norm], ignore_index = True)
    
#Access_Groups = open("Access_Groups_Modify.txt", "w")
#Access_Groups.write(group_access_df)
#Access_Groups.close()
group_access_df = group_access_df[['id','name','access','user_id']]
grp_mod = group_access_df
print("Modify Access for Groups successfully downloaded")
# Logout
logout(sess)
grp_mod = grp_mod[grp_mod['id'].isin(PinList_created)]
grp_mod['type'] = 'LIVEBOARD'
grp_mod


Call to '/callosum/v1/tspublic/v1/session/login' successfull! (204)

Call to '/callosum/v1/tspublic/v1/group' successfull! (200)
4881af30-aeee-49a3-9606-55cedeb23a66

Call to '/callosum/v1/tspublic/v1/metadata/listas?offset=-1&batchsize=2000&principalid=4881af30-aeee-49a3-9606-55cedeb23a66&minimumaccesslevel=MODIFY&type=USER_GROUP' successfull! (200)
Empty DataFrame
Columns: []
Index: []
2bec5a06-5068-471f-8afd-d61871c40207

Call to '/callosum/v1/tspublic/v1/metadata/listas?offset=-1&batchsize=2000&principalid=2bec5a06-5068-471f-8afd-d61871c40207&minimumaccesslevel=MODIFY&type=USER_GROUP' successfull! (200)
Empty DataFrame
Columns: []
Index: []
84b6709d-4b71-45df-aeed-da01c52ef1fb

Call to '/callosum/v1/tspublic/v1/metadata/listas?offset=-1&batchsize=2000&principalid=84b6709d-4b71-45df-aeed-da01c52ef1fb&minimumaccesslevel=MODIFY&type=USER_GROUP' successfull! (200)
Empty DataFrame
Columns: []
Index: []
6cb62f9c-9e89-42b6-a59d-be924c1aecf7

Call to '/callosum/v1/tspublic/v1/metadata/lis

/var/folders/72/k44_gp394l5g9rc09_hz25180000gs/T/ipykernel_8581/129437694.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  grp_mod['type'] = 'LIVEBOARD'


id  \
0   c05a39dc-3838-435d-bec5-62ff16df290c   
1   e0029dda-0b40-46b8-9637-3d5464cac065   
2   3a443655-b544-473f-9df2-d44006899c3e   
3   ad96fb40-d9b6-4350-afab-e009b2f49c34   
4   c12cbc23-a419-49fd-be9f-0ba202c87281   
5   f74fee53-2892-4623-bead-a1464cc24b9d   
6   a17acd34-a77d-4c1f-ac1f-98efc1418a9c   
7   6b771d58-133a-4167-bd0e-c615d44a19b8   
8   de4fb9a2-8c9a-4a7e-a31f-8cadbb76bf5b   
9   8ffba0ac-2fde-4b71-b2ba-83ae2a742f2a   
10  c7ef6c8c-4ba8-40f4-8b4b-001a0cc6dc1b   
11  092f0716-e7aa-4bf1-b51b-a25aded568b3   
12  36645b1d-21bb-4f80-a14c-60dac32953f6   
13  400e954a-ec62-4553-9cd7-c38560ffdc08   
14  4db39dac-fbdd-40e8-b090-d7ccc78beb63   
15  af9fdf06-9452-45c0-9292-f62b11577b06   
16  453c93e9-4b59-4b64-ac51-f54ddbbc473d   
17  4dac9934-0f24-4138-a08f-f17ea54068ad   
18  9a173eb3-d3af-4238-ac61-d7c3d47f9072   
19  a5204dde-9c19-420c-8d22-eed5d6f0de4f   
20  4d3097cf-0629-4414-b292-9721a32f4dc2   
21  7b871a05-1f0c-444f-8f95-0e18423e7051   
22  5bacf773-cb63-4192-ba5c-b8b4fc0c8bcf   
23  94fd1b63-7d43-4074-97c4-e11229783da8   
24  cce6e2a4-4e7e-45b7-bed0-296086eb042e   
25  aa840b51-9e62-46f3-82ac-8b269b9a7ac0   
26  69ea12b1-d9af-494a-91fe-530faf40cca6   
27  8f675836-4e83-461e-bf6f-bdcd06b7defe   
28  afdb8960-feb0-4e3b-97c2-6c0d195bd3c2   
29  8e9a2786-c708-424a-80d9-dfa39204fbf2   
30  e927e2e9-ebe1-4649-9100-14be88e54349   
31  e35bb8e8-695d-4e32-bae0-fbf37bf545a2   
32  8827a47c-7198-4962-9798-c8d4bfd57dfb   
33  7dd9286c-671e-47b8-9dfb-fd113cfd99e4   
34  5198ad70-e6ef-41ae-bfbd-783596be4af1   
35  c97b0947-3f09-40c2-a3a8-c378d5e97f33   
36  da51f606-1eff-40d9-94aa-a29ac0bc8b15   
37  4534887d-3e70-466d-b130-dc349228ab78   
38  5019fc68-2868-481e-8327-228f9973bf36   
39  403143f9-ed6d-4e51-957c-35279d739bce   
40  8bc40756-242a-4f6e-8a95-034575fe5c52   
41  e76f5d64-e286-486d-85dc-2282f83ed5ab   
42  2f8a4c82-c95e-441d-ad2f-ce90d60c571d   
43  12a360c1-6880-4839-86cd-5e7cc8a897a3   
44  e6b239a6-5870-4e73-8bde-97363d73e440   
45  718e480b-c191-4a31-84ec-d1cc6754a9da   
46  c79e3244-10c8-4e33-90a5-9d77b1503103   
47  3570fb2e-48ab-4550-b97a-36c31fe188a6   
48  55baf16c-3075-4cde-867e-b10b62cedfc3   
49  7cad6069-93b7-4d6a-9c4a-efc632b13ef1   
50  0225b62d-35d0-458a-bd0a-e37b037f245c   
51  30662828-2b47-4138-a7cf-5acc0a0a966b   
52  9d29b03d-5c59-40d7-9761-edfb97a8424b   

                                                 name  access  \
0                                        Data Request  MODIFY   
1            Investments - Welcome Bonus Dashboard v2  MODIFY   
2                                 Country On boarding  MODIFY   
3                                           Jo's Book  MODIFY   
4         ZH Acquisition Dashboard - Marketing - Luna  MODIFY   
5                    Australia New account Conversion  MODIFY   
6                                        IAID Tracker  MODIFY   
7                                        Mary's board  MODIFY   
8                              Referral IAID tracking  MODIFY   
9                 APAC Client Trading value dashboard  MODIFY   
10                    Copy of Monthly MI Report (SFC)  MODIFY   
11                               Revenue Distribution  MODIFY   
12                               Revenue Distribution  MODIFY   
13                                              Alpha  MODIFY   
14                                         Test -luna  MODIFY   
15                                Client PnL Analysis  MODIFY   
16                              Copy of Find Accounts  MODIFY   
17                                     Monthly CRM UK  MODIFY   
18                       Copy of Regional BD Swticher  MODIFY   
19                              Copy of Find Accounts  MODIFY   
20                             Top Traded Instruments  MODIFY   
21           Copy of Rebates Dashboard - Distribution  MODIFY   
22                                  SFC Since 1st May  MODIFY   
23                               introducer reporting  MODIFY   
24                                  

In [6]:
# download all metaobjects a user can modify
# Start Session
sess = requests.Session()
# Login via API
login(sess)
user_map = pd.read_csv('User_names.csv', header=[0], delimiter= ',')
#print(user_map)
UserData = lstUserLists(sess).json()    
User_df = json_normalize(UserData)
User_df['name'] = User_df['name'].str.upper()
user_map['name'] = user_map['name'].str.upper()
User_df = pd.merge(User_df,user_map, left_on='name', right_on='name')
print(User_df)

UserList = User_df['author'].to_list()

json_print = {}
user_access_df = pd.DataFrame()
# for all groups in user list gather metaobjects
for i in UserList:
    print(i)
    resp = lstUserMetadataRead(sess,i).json()
    resp_norm = json_normalize(resp['headers'])
    #print(resp_norm)
    resp_norm['access'] = "READ_ONLY"
    resp_norm['user_id'] = i
    # print user id into json for each metaobject user has access to
    user_access_df = pd.concat([user_access_df,resp_norm], ignore_index = True)
    
#Access_Users = open("Access_Users_read_only.txt", "w")
#Access_Users.write(group_access_df)
#Access_Users.close()
user_access_df = user_access_df[['id','name','access','user_id']]
usr_read = user_access_df
print("READ_ONLY Access for Users successfully downloaded")
# Logout
logout(sess)
usr_read = usr_read[usr_read['id'].isin(PinList_created)]
usr_read['type'] = 'LIVEBOARD'
usr_read


Call to '/callosum/v1/tspublic/v1/session/login' successfull! (204)

Call to '/callosum/v1/tspublic/v1/user/list' successfull! (200)
                        name              displayName description  \
0                     SYSTEM  System Management Group         NaN   
1                     SYSTEM              System User         NaN   
2          DBUTLER@CMC.LOCAL                  dbutler               
3          DBUTLER@CMC.LOCAL                  dbutler               
4           FALLAN@CMC.LOCAL                   fallan               
..                       ...                      ...         ...   
373       ESHILINA@CMC.LOCAL                 eshilina               
374        KPOTTON@CMC.LOCAL                  kpotton         NaN   
375        KPOTTON@CMC.LOCAL                  kpotton         NaN   
376  TSHARMA-PRICE@CMC.LOCAL            tsharma-price         NaN   
377          BWOOD@CMC.LOCAL                    bwood               

           created       modified pri

TypeError: write() argument must be str, not DataFrame

In [20]:
# download all metaobjects a group can modify
# Start Session
sess = requests.Session()
# Login via API
login(sess)
user_map = pd.read_csv('User_names.csv', header=[0], delimiter= ',')
#print(user_map)
UserData = lstUserLists(sess).json()    
User_df = json_normalize(UserData)
User_df['name'] = User_df['name'].str.upper()
user_map['name'] = user_map['name'].str.upper()
User_df = pd.merge(User_df,user_map, left_on='name', right_on='name')
print(User_df)

UserList = User_df['author'].to_list()
json_print = {}
user_access_df = pd.DataFrame()
# for all groups in user list gather metaobjects
for i in UserList:
    print(i)
    resp = lstUserMetadataModify(sess,i).json()
    resp_norm = json_normalize(resp['headers'])
    #print(resp_norm)
    resp_norm['access'] = "MODIFY"
    resp_norm['user_id'] = i
    # print user id into json for each metaobject user has access to
    user_access_df = pd.concat([user_access_df,resp_norm], ignore_index = True)
user_access_df = user_access_df[['id','name','access','user_id']]
usr_mod = user_access_df
print("Modify Access for Users successfully downloaded")
# Logout
logout(sess)
usr_mod = usr_mod[usr_read['id'].isin(PinList_created)]
usr_mod['type'] = 'LIVEBOARD'
usr_mod


Call to '/callosum/v1/tspublic/v1/session/login' successfull! (204)

Call to '/callosum/v1/tspublic/v1/user/list' successfull! (200)
                        name              displayName description  \
0                     SYSTEM  System Management Group         NaN   
1                     SYSTEM              System User         NaN   
2          DBUTLER@CMC.LOCAL                  dbutler               
3          DBUTLER@CMC.LOCAL                  dbutler               
4           FALLAN@CMC.LOCAL                   fallan               
..                       ...                      ...         ...   
373       ESHILINA@CMC.LOCAL                 eshilina               
374        KPOTTON@CMC.LOCAL                  kpotton         NaN   
375        KPOTTON@CMC.LOCAL                  kpotton         NaN   
376  TSHARMA-PRICE@CMC.LOCAL            tsharma-price         NaN   
377          BWOOD@CMC.LOCAL                    bwood               

           created       modified pri

TypeError: write() argument must be str, not DataFrame

# Join Permissions to new objects

In [31]:
grp_mod = grp_mod[grp_mod['id'].isin(PinList_created)]
grp_mod['type'] = 'LIVEBOARD'
grp_mod

id  \
0   c05a39dc-3838-435d-bec5-62ff16df290c   
1   e0029dda-0b40-46b8-9637-3d5464cac065   
2   3a443655-b544-473f-9df2-d44006899c3e   
3   ad96fb40-d9b6-4350-afab-e009b2f49c34   
4   c12cbc23-a419-49fd-be9f-0ba202c87281   
5   f74fee53-2892-4623-bead-a1464cc24b9d   
6   a17acd34-a77d-4c1f-ac1f-98efc1418a9c   
7   6b771d58-133a-4167-bd0e-c615d44a19b8   
8   de4fb9a2-8c9a-4a7e-a31f-8cadbb76bf5b   
9   8ffba0ac-2fde-4b71-b2ba-83ae2a742f2a   
10  c7ef6c8c-4ba8-40f4-8b4b-001a0cc6dc1b   
11  092f0716-e7aa-4bf1-b51b-a25aded568b3   
12  36645b1d-21bb-4f80-a14c-60dac32953f6   
13  400e954a-ec62-4553-9cd7-c38560ffdc08   
14  4db39dac-fbdd-40e8-b090-d7ccc78beb63   
15  af9fdf06-9452-45c0-9292-f62b11577b06   
16  453c93e9-4b59-4b64-ac51-f54ddbbc473d   
17  4dac9934-0f24-4138-a08f-f17ea54068ad   
18  9a173eb3-d3af-4238-ac61-d7c3d47f9072   
19  a5204dde-9c19-420c-8d22-eed5d6f0de4f   
20  4d3097cf-0629-4414-b292-9721a32f4dc2   
21  7b871a05-1f0c-444f-8f95-0e18423e7051   
22  5bacf773-cb63-4192-ba5c-b8b4fc0c8bcf   
23  94fd1b63-7d43-4074-97c4-e11229783da8   
24  cce6e2a4-4e7e-45b7-bed0-296086eb042e   
25  aa840b51-9e62-46f3-82ac-8b269b9a7ac0   
26  69ea12b1-d9af-494a-91fe-530faf40cca6   
27  8f675836-4e83-461e-bf6f-bdcd06b7defe   
28  afdb8960-feb0-4e3b-97c2-6c0d195bd3c2   
29  8e9a2786-c708-424a-80d9-dfa39204fbf2   
30  e927e2e9-ebe1-4649-9100-14be88e54349   
31  e35bb8e8-695d-4e32-bae0-fbf37bf545a2   
32  8827a47c-7198-4962-9798-c8d4bfd57dfb   
33  7dd9286c-671e-47b8-9dfb-fd113cfd99e4   
34  5198ad70-e6ef-41ae-bfbd-783596be4af1   
35  c97b0947-3f09-40c2-a3a8-c378d5e97f33   
36  da51f606-1eff-40d9-94aa-a29ac0bc8b15   
37  4534887d-3e70-466d-b130-dc349228ab78   
38  5019fc68-2868-481e-8327-228f9973bf36   
39  403143f9-ed6d-4e51-957c-35279d739bce   
40  8bc40756-242a-4f6e-8a95-034575fe5c52   
41  e76f5d64-e286-486d-85dc-2282f83ed5ab   
42  2f8a4c82-c95e-441d-ad2f-ce90d60c571d   
43  12a360c1-6880-4839-86cd-5e7cc8a897a3   
44  e6b239a6-5870-4e73-8bde-97363d73e440   
45  718e480b-c191-4a31-84ec-d1cc6754a9da   
46  c79e3244-10c8-4e33-90a5-9d77b1503103   
47  3570fb2e-48ab-4550-b97a-36c31fe188a6   
48  55baf16c-3075-4cde-867e-b10b62cedfc3   
49  7cad6069-93b7-4d6a-9c4a-efc632b13ef1   
50  0225b62d-35d0-458a-bd0a-e37b037f245c   
51  30662828-2b47-4138-a7cf-5acc0a0a966b   
52  9d29b03d-5c59-40d7-9761-edfb97a8424b   

                                                 name  access  \
0                                        Data Request  MODIFY   
1            Investments - Welcome Bonus Dashboard v2  MODIFY   
2                                 Country On boarding  MODIFY   
3                                           Jo's Book  MODIFY   
4         ZH Acquisition Dashboard - Marketing - Luna  MODIFY   
5                    Australia New account Conversion  MODIFY   
6                                        IAID Tracker  MODIFY   
7                                        Mary's board  MODIFY   
8                              Referral IAID tracking  MODIFY   
9                 APAC Client Trading value dashboard  MODIFY   
10                    Copy of Monthly MI Report (SFC)  MODIFY   
11                               Revenue Distribution  MODIFY   
12                               Revenue Distribution  MODIFY   
13                                              Alpha  MODIFY   
14                                         Test -luna  MODIFY   
15                                Client PnL Analysis  MODIFY   
16                              Copy of Find Accounts  MODIFY   
17                                     Monthly CRM UK  MODIFY   
18                       Copy of Regional BD Swticher  MODIFY   
19                              Copy of Find Accounts  MODIFY   
20                             Top Traded Instruments  MODIFY   
21           Copy of Rebates Dashboard - Distribution  MODIFY   
22                                  SFC Since 1st May  MODIFY   
23                               introducer reporting  MODIFY   
24                                  

# Create new users

In [ ]:
import os
import requests
import string
import random
from Preamble import *
from thoughtspot_rest_api_v1 import *
# from src.thoughtspot_rest_api_v1.tsrestapiv1 import *

thoughtspot_server = ts_host2       # or type in yourself
service_acct_username = username2  # or type in yourself
service_acct_password = password2  # or type in yourself

ts: TSRestApiV1 = TSRestApiV1(server_url=thoughtspot_server)

# Wrapped in function to call as part of a retry loop when used in a long-running server / service process
def login():
    try:
        ts.session_login(username=service_acct_username, password=service_acct_password)
    except requests.exceptions.HTTPError as e:
        print(e)
        print(e.response.content)


login()

def create_user(rest_api_obj: TSRestApiV1, username, display_name, email, groups_guid):

    # REST API requires setting a password for users, but it is never used with SSO
    # Randomly generate password and set it when creating using
    letters = string.ascii_letters
    user_password = ''.join(random.choice(letters) for i in range(20))

    new_user_guid = rest_api_obj.user_post(username=username, password=user_password, display_name=display_name,
                                           properties = None,groups=groups_guid)

In [ ]:
for i in range(len(new_user_objects)):
    try:
        username = new_user_objects['header.name'].iloc[i]
        displayname = new_user_objects['header.displayName'].iloc[i]
        email = new_user_objects['userContent.userProperties.mail'].iloc[i]
        group_guid = new_user_objects['assignedGroups'].iloc[i]
        create_user(rest_api_obj=ts, username=username, display_name=displayname,
                            email=email, groups_guid=group_guid)
        print(username+ " successfully created")
    except:
        pass
